In [3]:
import numpy as np
import matplotlib.pyplot as plt
import random as rand
from sklearn import datasets, linear_model
import copy as cp
from ipywidgets import interact, interactive, fixed, interact_manual
import ipywidgets as widgets
from mpl_toolkits.mplot3d import Axes3D

import numpy.random as randn
from sklearn.linear_model import LinearRegression
from sklearn.linear_model import Ridge
from sklearn.linear_model import ElasticNet
from sklearn.preprocessing import PolynomialFeatures
from sklearn.linear_model import LinearRegression
from sklearn.pipeline import Pipeline
from sklearn import preprocessing
from sklearn.linear_model import Lasso

import plotly.graph_objects as go
from plotly.subplots import make_subplots
import plotly.offline as py
import copy 

# Régression

## Principe de la régression 

La **régression** est un processus d'apprentissage supervisé qui consiste à construire un modèle prédictif à partir de données quantitatives.

On considère un observation $X$ (pouvant être vectoriel) et une sortie $y$ scalaire ici (mais pouvant être vectoriel) tel que

$$
y=f(X)+ \epsilon
$$

avec une fonction (transformation) inconnue et $\epsilon$ un bruit sur les données.

**But**: $\color{red}{\text{approcher $f$ à partir d'un jeu d'apprentissage $((X_1,y_1),....,(X_n,y_n))$}}$.

**Exemple**:
    
- $X$ = nombre d'année d'étude (dimension 1), $y$ = salaire moyen
- $X$ = image d'une radiographie d'organe (dimension $10^6$), $y$ = même image mais "surlignant" un potentiel cancer.

**Dimension**: $\color{red}{\text{nombre de paramètres indépendant définissant un objet}}$.

- **Une position** dans le monde physique est un objet de dimension 3 car il faut 3 paramètres pour la définir (longueur, largeur, hauteur)
- **Une image** est un objet de dimension $N$ (nombre de pixel) car informatiquement deux images sont différentes si un seul pixel change. Il faut donc les $N$ pixels pour définir une image.

**Différence avec la classification**:
 
En classification $y$ vaut une valeur parmis les entiers $\left\{1,2 ... ,K\right\}$. En régression $y$ peut valoir une valeur quelconque.

**Modèle Paramétrique**:

On se donne une fonction $f_{\theta}$ connue mais dépendante de paramètres (nombres) **inconnus**.

En $\color{red}{\text{apprentissage supervisé}}$ on va trouver les **paramètres $\theta$** tel que $f_{\theta}(X)$ $\color{red}{\text{prédit au mieux le $y$ associé à $x$}}$.

$\theta$ peut prendre plein de valeur possible donc il existe beaucoup de modèles possibles.

Pour effectuer cette **régression** que faut t'il:
- choisir un modèle paramétrique $f_{\theta}$
- choisir un critère pour déterminer les paramètres $\theta$,
- effectuer l'apprentissage sur le jeu de données d'exemples,
- valider le modèle obtenu.

## Régression linéaire

**Fonction linéaire/affine**: fonctions les plus simples, la dépendance à une entrée $x$ est de type $ax+b$

- $X=(x,y)$ (dimension 2), $f(x,y)=ax+by+c$ est linéaire,
- $X=x$ (dimension 1), $f(x)=a x^2$ n'est pas linéaire,
- $X=(x,y,z)$ (dimension 3), $f(x,y,z)=ax+by+0.0001 cos(z)sin(x)$, non linéaire mais presque linéaire.

La régression **linéaire** consiste à
- supposer que la fonction $f$ inconnu est **linéaire/affine** ou presque.
- choisir un modèle paramétrique linéaire/affine par rapport à l'observation $X$,
- choisir comme critère de sélection du modèle: $\color{red}{\text{minimiser la distance entre la prédiction et la vraie sortie sur le jeu de données d'exemples}}$.

**Exemple**: On cherche à comprendre comment des facteurs de risques influent sur le poids du bébé à la naissance.

On propose comme facteur explicatifs:
- l'âge de la mère,
- la poids de la mère,
- consommation d'alcool en verre par semaine (de 0 à 20),
- tabagisme en cigarette par semaine (de 0 à 50).

On propose le modèle suivant:
    
$$
PBEBE= a_0 + a_1 PMERE + a_2 AGE + a_3 ALCOOL + a_4 TABAC + \epsilon
$$

Si on détermine $(a_0,a_1,a_2,a_3,a_4)$ qui explique bien $PBEBE$ on pourra déterminer le facteur principal. Celui dont le paramètre $a_i$ sera le plus grand.

Cas général:
- si $X=x$ est un nombre
$$
f_{\theta}(x)=\omega x + b
$$

avec $\theta=(\omega,b)$ les paramètres à déterminer.
- si $X=(x_1,...x_d)$ est un vecteur en taille $d$
$$
f_{\theta}(X)=\sum_{i=1}^d \omega_i x_i + b
$$

avec $\theta=(\omega_1,...\omega_d,b)$ les paramètres à déterminer.

Pour déterminer les paramètres, on souhaite résoudre

$$
\operatorname{min}_{\theta}J(\theta)=\sum_{i=1}^n d_2(y_i,f_{\theta}(X_i))^2
$$

avec $d_2(y_1,y_2)$ une distance entre 2 nombres.

- pour $d=1$ cela revient à trouver la droite qui minimise la distance aux points $y$ du jeux d'apprentissage,
- pour $d=2$ cela revient à trouver le plan qui minimise la distance aux points $y$ du jeux d'apprentissage.

On appelle $\color{red}{\text{$J$ la fonction coût ou la "loss"}}$.

**Exemple de régression en dimension 1**:

- en rouge les points $(x,y)$ d'exemple,
- en noir la droite (modèle de régression) qui pour un $x$ predit un $y$,
- en gris la distance entre les exemples et le modèle.

In [4]:
def droite1(x):
    return 1.3*x+2.0

def plot_line(n,bruit):
    x_plot= np.linspace(0.0,1.0,n)
    y_train=np.zeros(n)
    eps = np.random.normal(0.0,bruit,n)
    y_train[:] = droite1(x_plot[:])+eps[:]

    
    fig = make_subplots(rows=1, cols=1) 
    #ax1.set_ylim([1.5,4.0])
    fig.add_trace(go.Scatter(x=x_plot,y=y_train,mode="markers", marker_size=10,marker_color='red')) 
    fig.add_trace(go.Scatter(x=x_plot,y=droite1(x_plot),line_dash="dashdot",line_color='black'))         
    for i in range(0,n):
        xloc=[x_plot[i],x_plot[i]]
        yloc=[droite1(x_plot[i]),y_train[i]]
        fig.add_trace(go.Scatter(x=xloc,y=yloc,line_width=4,line_color="gray",opacity=0.5)) 
    fig.update_layout(showlegend=False)
    fig.show()

In [5]:
@interact(n=(10,100,1),bruit=(0.0,0.2,0.01))
def plot1(n=20,bruit=0.0):
    plot_line(n,bruit)

interactive(children=(IntSlider(value=20, description='n', min=10), FloatSlider(value=0.0, description='bruit'…

### Comment résoudre le problème de minimisation

En pratique, les librairies de calcul calculeront pour vous la solution.

Mais intéressant de savoir comment on peut trouver une solution.

Utile pour $\color{red}{\text{comprendre pourquoi ça peut ne pas marcher et comment régler le problème}}$.

**Résultat mathématique** (à admettre):

- $d$ la taille des vecteurs d'observation $X$.

Si $N$ le nombre d'exemples est supérieur $d+1$ (nombre de paramètres) **il existe une unique solution**.

Donc il existe un seul $\theta=(\omega,b)$ qui minimise l'erreur sur les données.

**Exemple**:

- X=x (dim 1), la fonction à trouver/approcher est $y=f(x)=\frac12 x+ 3.5$.
- On se donne $f_{\theta}=w x + b$ avec $\theta=(\omega,b)$ à déterminer.
- On se donne $N$ exemples $((x_1,y_1),...,(x_n,y_n))$.

In [6]:
def droite_loss(x):
    return 0.5*x+3.5

def data(nb_point,bruit):
    
    x_train = np.random.uniform(-1.0,1.0,nb_point)
    eps = np.random.normal(0.0,bruit,nb_point)
    y_train = droite_loss(x_train)+eps

    return x_train,y_train

def loss(omega,b,x_train,y_train):
    J=0.0
    J_w=0.0
    J_b=0.0
    n= np.shape(x_train)[0]
    for i in range(0,n):
        J=J+ (y_train[i]-omega*x_train[i]-b)**2.0
        J_w =J_w- x_train[i]*(y_train[i]-omega*x_train[i]-b) 
        J_b=J_b-(y_train[i]-omega*x_train[i]-b) 
    return J/n,J_w/n,J_b/n

def plot_loss_loc(nb_point,bruit):
    n=200
    np.random.seed(50)
    xt,yt=data(nb_point,bruit)
    xtt=xt.reshape(-1,1)
    ridge = Ridge(alpha=0.0,tol=10-10).fit(xtt,yt)
    
    tw = np.linspace(-30.0,30,n)
    tb = np.linspace(-4.0,12.0,n)
    
    tw_mg,tb_mg=np.meshgrid(tw,tb)
    J_mg= loss(tw_mg,tb_mg,xt,yt)[0]
    fig = go.Figure()
    fig.add_trace(go.Surface(x=tw_mg, y=tb_mg, z=J_mg, cmid=0, colorscale="Jet",opacity=0.5))
    fig.add_trace(go.Scatter3d(x=[0.5], y=[3.5], z=[0.0],mode='markers',marker_size=5,marker_color='red'))
    fig.add_trace(go.Scatter3d(x=ridge.coef_, y=[ridge.intercept_], z=[0.0],mode='markers',marker_size=8,marker_color='blue',opacity=0.75))
    fig.update_layout(height=500, width=800, margin=dict(l=35, r=30, b=45, t=60),showlegend=False)
    fig.show()

- On trace $J(\theta)=J(\omega,b)$ l'erreur, faite par $f_{\theta}(x)$ sur les exemples, en fonction de $(\omega,b)$

- En rouge la solution $(\frac12,3.5)$ en bleu le minimum de $J(\omega,b)$

In [7]:
@interact(n=(10,100,1),bruit=(0.0,0.2,0.01))
def plot2(n=20,bruit=0.0):
    plot_loss_loc(n,bruit)

interactive(children=(IntSlider(value=20, description='n', min=10), FloatSlider(value=0.0, description='bruit'…

Il existe $\color{red}{\text{beaucoup de méthodes de résolution}}$.

On va regarder une méthode classique peu utilisée en régression (car il existe plus efficace dans ce cas simple) mais très utilisée en **Deep-learning** (cas plus général).

On parle de **méthode du gradient**.

Le **gradient** est un objet mathématique qui décrit le **taux d'accroissement locale de la fonction**.

On ne va pas rentrer dans les détails mathématiques. Explication $\color{red}{\text{géométrique}}$:

On va regarder la parabole $f(x)=ax^2+bx+2$ pour montrer le gradient. Les **fonctions de coût** sont des paraboles en plus grande dimension.

In [8]:
 def parabole(x,a,b):
        return a*x*x+b*x+2.0
    
def tangeante(x,x1,x2,y1,y2):
    a=(y2-y1)/(x2-x1)
    b=y1-a*x1
    return a*x+b
    
def plot_tangeante(a,b,xref):
    n=200
    x=np.linspace(-20.0,20.0)
    y=parabole(x,a,b)
    yt=tangeante(x,xref,xref+0.0001,parabole(xref,a,b),parabole(xref+0.0001,a,b))
    
    fig = go.Figure()  
    fig.update_yaxes(range=(-100.0,1000.0))
    fig.add_trace(go.Scatter(x=x,y=y,name="parabole",line_width=4,line_color="black",line_dash="dashdot",opacity=0.9)) 
    fig.add_trace(go.Scatter(x=x,y=yt,name="dérivée",line_width=4,line_color="red",line_dash="solid",opacity=1.0)) 
    fig.add_trace(go.Scatter(x=[xref],name="point dev",y=[parabole(xref,a,b)],mode="markers", marker_size=10,marker_color='blue')) 
    fig.show()

**Gradient et Parabole**:

In [9]:
@interact(a=(1,5.0,0.5),b=(1,5.0,0.5),xref=(-20.0,20.0,0.25))
def plot3(a=3.5,b=3.5,xref=15.0):
    plot_tangeante(a,b,xref)

interactive(children=(FloatSlider(value=3.5, description='a', max=5.0, min=1.0, step=0.5), FloatSlider(value=3…

**Remarque essentielle**: 

Le **gradient est nul** au minimum de la courbe, ce qui veut dire qu'il n'y pas d'accroissement local en un minimum.

On note le gradient $\nabla f(x)$ de la fonction $f$. Soit $x_m$ un minimum dans ce cas:

$$
\nabla f(x_m)=0
$$

$\color{red}{\text{Si le minimum est unique il y a unique point ou le gradient est nul}}$.

**Méthode de gradient**

On va successivement bouger les paramètres $\theta=(\omega,b)$ dans la direction de descente du gradient de $J(\theta)$ ce qui revient à:

$\color{red}{\text{à bouger les paramètres dans la direction qui fait baisser la fonction coût donc l'erreur sur les données}}$.

Cela s'écrit

$$
\theta^{(k)}=\theta^{(k-1)}-\eta \nabla J(\theta^{(k)})
$$

avec $(\theta^{(1)},....,\theta^{(k)})$ une succession de paramètres. Plus on avance dans cette succession de paramètres, plus le gradient devient faible et donc plus on se rapproche du minimum.

In [10]:
def plot_gradient(nb_point,bruit,eta,ig):
    n=100
    np.random.seed(50)
    xt,yt=data(nb_point,bruit)
    xtt=xt.reshape(-1,1)
    ridge = Ridge(alpha=0.0,tol=10-10).fit(xtt,yt)
    
    tw = np.linspace(-30.0,30,n)
    tb = np.linspace(-4.0,12.0,n)
    
    tw_mg,tb_mg=np.meshgrid(tw,tb)
    J_mg= loss(tw_mg,tb_mg,xt,yt)[0]
    w0= [tw[90]]
    b0= [tb[90]]
    l0 =[loss(w0[-1],b0[-1],xt,yt)[0]]

    for i in range(0,ig):
        wc=w0[-1]
        bc=b0[-1]
        w0.append(wc-eta*loss(wc,bc,xt,yt)[1])
        b0.append(bc-eta*loss(wc,bc,xt,yt)[2])
        l0.append(loss(w0[-1],b0[-1],xt,yt)[0])
    
    fig = go.Figure()
    fig.add_trace(go.Surface(x=tw_mg, y=tb_mg, z=J_mg, cmid=0, colorscale="Jet",opacity=0.5))
    fig.add_trace(go.Scatter3d(x=[0.5], y=[3.5], z=[0.0],mode='markers',marker_size=5,marker_color='red'))
    fig.add_trace(go.Scatter3d(x=ridge.coef_, y=[ridge.intercept_], z=[0.0],mode='markers',marker_size=8,marker_color='blue',opacity=0.75))
    fig.add_trace(go.Scatter3d(x=w0, y=b0, z=l0, marker_color="green",opacity=0.9,marker_size=4))
    fig.update_layout(height=500, width=800, margin=dict(l=35, r=30, b=45, t=60),showlegend=False)
    fig.show()

- On retrace $J(\theta)=J(\omega,b)$ l'erreur, faite par $f_{\theta}(x)$ sur les exemples, en fonction de $(\omega,b)$ (même exemple qu'avant).

- En rouge la solution $(\frac12,3.5)$ en bleu le minimum de $J(\omega,b)$. En vert un choix initial de $(\omega,b)$.

In [11]:
@interact(nb_point=(1,20,1),bruit=(0.02,0.05,0.005),eta=(0.2,2.0,0.1),ig=(0,100,5))
def plot4(nb_point=10,bruit=0.05,eta=0.1,ig=0):
    plot_gradient(nb_point,bruit,eta,ig)

interactive(children=(IntSlider(value=10, description='nb_point', max=20, min=1), FloatSlider(value=0.05, desc…

Un paramètre important est $\eta$ le **taux d'apprentissage**.

$\color{red}{\text{Vous le retrouverez beaucoup en apprentissage profond}}$.

On voit que petit, on descend trop lentement. Trop grand on va descendre en oscillant ce qui n'est pas efficace (ça peut même empêcher la méthode de marcher).

Il faut donc **prendre $\eta$ si trop grand ni trop petit** et choisir la valeur de ce paramètre sera une des choses que vous devrez tester en apprentissage profond.

### Régression et malediction en grande dimension

In [12]:
def droite(x):
    return 1.3*x+2.0

def plot_multi_droite(nb_point,bruit):
    n=100
    x_train= np.zeros((nb_point,1))
    x_plot= np.zeros((n,1))
    y_train= np.zeros((nb_point,1))
    
    
    x_plot[:,0] = np.linspace(0.0,2.0,n)
    x_train[:,0] = np.random.uniform(0.0,2.0,nb_point)
    eps = np.random.normal(0.0,bruit,nb_point)
    y_train[:,0] = droite(x_train[:,0])+eps[:]
    
    regr = linear_model.Ridge(alpha=0.0)
    regr.fit(x_train, y_train)    
    fig = go.Figure()
    fig.add_trace(go.Scatter(x=x_train[:,0], y=y_train[:,0],mode='markers',marker_size=10,marker_color='red'))
    if nb_point > 1:
        fig.add_trace(go.Scatter(x=x_plot[:,0], y=regr.predict(x_plot)[:,0],line_color='blue',line_width=4))
    else:
        a = regr.coef_
        b = regr.intercept_
        for i in range(0,10):
            b= y_train[0,0]-(a+i*0.2)*x_train[0,0]
            y = (a+i*0.2)*x_plot+b
            fig.add_trace(go.Scatter(x=x_plot[:,0], y=y[:,0],line_width=4))
            
    fig.add_trace(go.Scatter(x=x_plot[:,0], y=droite(x_plot[:,0]),line_color='black',line_width=4,line_dash="dashdot"))
    fig.update_layout(showlegend=False)
    fig.show()

La théorie dit que tout va bien si $N>d+1$. 

Lorsque $d$ (taille des observations) est très grand on risque d'avoir $d+1>N$.

Que se passe t'il dans ce cas ?

Exemple d=1 donc $2$ paramètres :

In [13]:
@interact(nb_point=(1,20,1),bruit=(0.02,0.05,0.005))
def plot5(nb_point=10,bruit=0.05):
    plot_multi_droite(nb_point,bruit)

interactive(children=(IntSlider(value=10, description='nb_point', max=20, min=1), FloatSlider(value=0.05, desc…

**Résultat théorique**:
- $N>d+1$  on a unicité du $\theta=(\omega,b)$ qui minimise l'erreur,
- $N=d+1$  on a unicité du $\theta=(\omega,b)$ qui minimise l'erreur et on passe exactement par les exemples,
- $d+1>N$   on a pas unicité du $\theta=(\omega,b)$ qui minimise l'erreur, et on passe exactement par les points. $\color{red}{\text{Il existe donc une infinité de modèles possibles dont le bon}}$.

**Problèmes pour le cas d=1** (droite):
- cas $d+1>N$: le modèle peut construire une droite totalement différente de la bonne droite. On sera bon sur l'exemple d'apprentissage mais très mauvais ailleurs.
- cas $d+1=N$: si pas de bruit, on obtient la bonne droite. Si il y a du bruit on apprend le bruit.

**Mais**: *Par contre si $N>>d+1$ et si il y a du bruit on apprend peu le bruit*.

**Exemple de perte d'unicité**:

- On retrace $J(\theta)=J(\omega,b)$ l'erreur, faite par $f_{\theta}(x)$ sur les exemples, en fonction de $(\omega,b)$ (même exemple qu'avant).

- En rouge la solution $(\frac12,3.5)$ en bleu le minimum de $J(\omega,b)$. En vert un choix initial de $(\omega,b)$.

In [14]:
@interact(nb_point=(1,20,1),bruit=(0.02,0.05,0.005),eta=(0.2,2.0,0.1),ig=(0,100,5))
def plot6(nb_point=10,bruit=0.05,eta=0.1,ig=0):
    plot_gradient(nb_point,bruit,eta,ig)

interactive(children=(IntSlider(value=10, description='nb_point', max=20, min=1), FloatSlider(value=0.05, desc…

**Régression linéaire**: quand $d+1$ est proche de $N$ ou supérieur on apprend très bien les exemples mais à cause de la non-unicité du modèle on peut avoir $\color{red}{\text{un modèle qui se généralise très mal à des nouvelles données}}$. 

Lorsqu'un modèle se généralise mal à des nouvelles données, on parle de **sur-apprentissage**.

In [15]:
def generate_data(sigma,beta,alpha,n,m): ## génère n exemple dans R^m avec le modèle $f$
    X = np.zeros((n,m)) ## creation de la matrice à n exemple de dimension m
    Y = np.zeros(n) ## creation de la matrice à n exemple de dimension l
    Xhat = np.zeros((n,m)) ## creation de la matrice à n exemple de dimension m
    Yhat = np.zeros(n)
    eps = randn.normal(0.0,sigma,n) ## vecteur des bruits
    meanY = 0.0
    meanX = np.zeros(m)
    varianceX = np.zeros(m)
    for i in range(0, n):
        X[i,:]=randn.uniform(0.0,2.0,m) # m nombre aléatoire entre 0 et 1
        Y[i]= np.dot(beta,X[i,:])+alpha+eps[i]
        meanX[:] = meanX + X[i,:]/n
        meanY = meanY + Y[i]/n 
        varianceX[:] = varianceX[:] + X[i,:]*X[i,:]/n
        
    for i in range(0, n):
        Xhat[i,:]= (X[i,:]-meanX[:])/(varianceX[:])
        Yhat[i]= (Y[i]-meanY)
    
    return X,Y,eps

In [16]:
# calcul les erreur pour la regression Rdige
def errorR(lam,beta_hat,alpha_hat,X,Y,n,m):
    nnew=100
    if lam >0:
        reg = Ridge(alpha=lam,tol=10-12,solver='svd').fit(X,Y)
    else: 
        reg = LinearRegression().fit(X, Y)
     
    Yref = np.zeros(n); Ycom = np.zeros(n)   
    Ynewref = np.zeros(nnew); Ynewcom = np.zeros(nnew)
       
    Xnew = np.zeros((nnew,m)) # entrées et sortiesde l'échantillon de test
    for i in range(0, nnew):
        Xnew[i,:]=randn.uniform(0.0,2.0,m)   
        Ynewref[i]= np.dot(beta_hat,Xnew[i,:])+alpha_hat
        Ynewcom[i] = np.dot(reg.coef_,Xnew[i,:])+reg.intercept_

    for i in range(0, n): # sortie de l'échantillon d'entrainement
        Ycom[i] = np.dot(reg.coef_,X[i,:])+reg.intercept_
        Yref[i]= np.dot(beta_hat,X[i,:])+alpha_hat

    Error=0.0;  ErrorQuad=0.0; normp=0.0

    Error = np.mean((Ynewref - Ynewcom)**2)
    ErrorQuad = np.mean((Y - Ycom)**2) 

    normp = reg.intercept_**2
    for i in range(0,m):
        normp = normp+reg.coef_[i]**2
    normp/(m+1) 
    return Error,ErrorQuad,normp

In [17]:
def plot_overfitting_dim(bruit,dim): ## affiche les erreurs pour une regréssion classique
    n = 100 
    EQ=[]; E=[]; B=[]; V=[]; iterl=[] ## liste de stockage
    for m in range(10,dim,5):
        beta= randn.uniform(-1.0,1.0,m)
        alpha = randn.uniform(-1.0,1.0)
        X,Y,eps= generate_data(bruit,beta,alpha,n,m)
        Error,ErrorQuad,normp = errorR(0.0,beta,alpha,X,Y,n,m)
        E.append(Error); EQ.append(ErrorQuad); iterl.append(m)

    fig = make_subplots(rows=1, cols=2) 
    fig.add_trace(go.Scatter(x=iterl, y=E,line_width=3,line_color='blue'), row=1, col=1)
    fig.update_layout(
        title_text="Erreur sur nouvelles données"          
    )
    if dim>100:
        fig.add_vline(x=100,line_color='red')

    fig.add_trace(go.Scatter(x=iterl, y=EQ,line_width=3,line_color="blue"), row=1, col=2)
    if dim>100:
        fig.add_vline(x=100,line_color='red')
    fig.update_layout(height=300, width=900, margin=dict(l=35, r=30, b=45, t=60),showlegend=False)
    fig.show()

**Exemple en grande dimension**.

$$
y=f(X)+\epsilon 
$$

avec $f(X)=\sum_{i=1}^d \alpha_i x_i + \beta$ et $(\alpha_1,....,\alpha_d)$ choisis aléatoirement. On l'approche avec

$$
f_{\theta}(X)=\sum_{i=1}^d \omega_i x_i + b
$$

**Régression avec N=100 exemples**. On fait varier $d$ la taille de $X$. 
- Gauche: erreur sur les données exemples (données d'apprentissage),
- Droite: erreur sur de nouvelles données

In [18]:
@interact(bruit=(0.02,0.05,0.005),dim=(20,400,10))
def plot7(bruit=0.05,dim=20):
    plot_overfitting_dim(bruit,dim)

interactive(children=(FloatSlider(value=0.05, description='bruit', max=0.05, min=0.02, step=0.005), IntSlider(…

**Modèle généraux**: si un modèle est trop complexe, a trop de paramètres par rapport aux nombres d'exemples, l'apprentissage peut échouer. Pour les problèmes linéaires cela vient d'une perte d'unicité.

Dans ce cas, il existe beaucoup de jeux de paramètres qui modélisent parfaitement les exemples, y compris de très mauvais jeux de paramètres.

**Modèle généraux**:

En général le problème ne vient pas d'une perte d'unicité, comme pour les modèles linéaires. En effet il y a rarement unicité dans la vraie vie mais plein de bon jeux de paramètres (proche du bon).


$\color{red}{\text{Mais si le nombre de paramètres devient trop grand ou les modèle trop riches}}$:

- on peut bien apprendre les données mais quand même tombé sur un mauvais jeu de paramètres.
- on apprend tellement bien les données qu'on apprend le bruit.
- on apprend tellement bien les données qu'on apprend les défauts du jeux d'apprentissage (surreprésentation de certaines données etc).

**Exemple**: polynôme

$$
P_k(x)=a_0 + a_1x + a_2x^2 + .... a_n x^n
$$

Idée: on utilise comme fonction paramètrique des polynômes. Exemple en dimension 1:

$$
f_{\theta}(x)=P_k(x)
$$

La régression linéaire est équivalent à $k=1$.



In [19]:
def true_fun(X):
    return  np.cos(1.0 * np.pi * X)

np.random.seed(0)

def plot_overfitting(n_samples):
    degrees = [1, 2, 5, 18]

    X = np.random.uniform(-1.0,1.0,n_samples)
    y = true_fun(X) + np.random.randn(n_samples) * 0.1
    
    fig = make_subplots(rows=1, cols=5) 
    for i in range(0,len(degrees)):
        polynomial_features = PolynomialFeatures(degree=degrees[i],
                                             include_bias=False)
        linear_regression = LinearRegression()
        pipeline = Pipeline([("polynomial_features", polynomial_features),
                         ("linear_regression", linear_regression)])
        pipeline.fit(X[:, np.newaxis], y)

        X_test = np.linspace(-1.0, 1.0, 100)
        fig.add_trace(go.Scatter(x=X_test, y= pipeline.predict(X_test[:, np.newaxis]),
                                 line_width=5,line_color='orange'), row=1, col=i+1)
        fig.add_trace(go.Scatter(x=X_test, y= true_fun(X_test),
                                 line_width=2,line_color='black',opacity=0.7),row=1, col=i+1)
        fig.add_trace(go.Scatter(x=X, y=y,mode='markers',
                                 marker_size=5,marker_color='blue',opacity=0.4), row=1, col=i+1)
        fig.update_xaxes(range=(-1.1,1.1))
        fig.update_yaxes(range=(-2.0,2.0))
    fig.update_layout(height=400, width=900, margin=dict(l=35, r=30, b=45, t=60),showlegend=False)
    fig.show()

**Exemple de sur-apprentissage avec un modèle polynomial**:

On compare 4 valeurs de $K= [1, 2, 5, 18]$

- En rouge la vrai fonction $f(x)=sin(x)$, en orange la prédiction. 
- En bleu les exemples.

In [20]:
@interact(n_samples=(20,200,10))
def plot8(n_samples=200):
    plot_overfitting(n_samples)

interactive(children=(IntSlider(value=200, description='n_samples', max=200, min=20, step=10), Output()), _dom…

Ici on a $K+1$ paramètres ( donc au maximum 19).

Même avec 20 et 40 points on voit le **sur-apprentissage**. Ici on est dans un cas où le nombre de paramètres n'est pas supérieur aux nombres d'exemples mais ou le $\color{red}{\text{modèle est trop complexe}}$.

En effet un polynôme de degré 18 peut être une fonction **très oscillante** (si les dernières coefficients sont importants) et donc il est difficile de représenter notre fonction si on a peu de points car $\color{red}{\text{on laisse trop de liberté au modèle}}$ et il va trop osciller.

## Régularisation

Comment régler le sur-apprentissage ?

On a vu qu'il apparaissait quand:
- le nombre de paramètres est trop grand,
- le modèle est trop complexe.

Dans les deux cas: **trop de liberté laisser au modèle** qui capture très bien les données au risque de pas savoir généraliser

**Solution**: $\color{red}{\text{contraindre le modèle à être plus simple ou contraindre les paramètres}}$.

### Régression Ridge

La première solution est appelée **Régression Ridge**.

Il s'agit de résoudre le problème

$$
\operatorname{min}_{\theta}J(\theta)=\sum_{i=1}^n d_2(y_i,f_{\theta}(x_i))^2
$$

sous la contrainte $d_2(\theta,0)^2\leq \tau$.

La contrainte revient à dire qu'on veut que les $\color{red}{\text{paramètres soit proches de zéro}}$.

La contrainte porte sur l'ensemble des poids ($\theta$ représente tous les poids). Un point peut être éloigné de zéro mais dans ce cas les autres en seront d'autant plus proche.

**Logique**: en ajoutant une contrainte on laisse moins de **liberté au modèle**.

- **Cas linéaire**: on avait trop de paramètres donc trop de modèle possible, on contraint leurs valeurs donc on réduit les possibilités.

- **Cas Polynomial**: On a un modèle trop complexe. En limitant la taille des paramètres notamment des derniers ($a_{12}$,...$a_{18}$ par exemple) on limite la complexité du modèle (la capacité à osciller ici).

La contrainte est difficile à gérer. $\color{red}{\text{Sous cette forme on parle de contrainte forte}}$.

**Contrainte faible**:

$$
\operatorname{min}_{\theta}J(\theta)=\sum_{i=1}^n d_2(y_i,f_{\theta}(x_i))^2 +\lambda d_2(\theta,0)^2
$$

On impose pas $d_2(\theta,0)^2\leq \tau$ mais on minimise $d_2(\theta,0)^2$.

On minimise donc l'erreur en minimisant aussi la taille des paramètres. Plus $\lambda$ est grand plus la contrainte est forte.


On avait vu que le sur-apprentissage venait d'une perte d'unicité de la solution du problème de minimisation.
**Que se passe t'il ici ?**

On reprend l'exemple précédent avec la descente de gradient:

In [21]:
def data2(nb_point,bruit):
    
    x_train = np.random.uniform(-1.0,1.0,nb_point)
    eps = np.random.normal(0.0,bruit,nb_point)
    y_train = droite_loss(x_train)+eps

    return x_train,y_train

def loss2(reg,omega,b,x_train,y_train):
    J=0.0
    J_w=0.0
    J_b=0.0
    n= np.shape(x_train)[0]
    for i in range(0,n):
        J=J+ (y_train[i]-omega*x_train[i]-b)**2.0 + reg*omega**2.0 + reg*b**2.0
        J_w =J_w- x_train[i]*(y_train[i]-omega*x_train[i]-b) + reg*2.0*omega
        J_b=J_b-(y_train[i]-omega*x_train[i]-b) + reg*2.0*b
    return J/n,J_w/n,J_b/n

In [22]:
def plot_gradient2(nb_point,bruit,eta,ig,reg):
    n=100
    np.random.seed(50)
    xt,yt=data2(nb_point,bruit)
    xtt=xt.reshape(-1,1)
    ridge = Ridge(alpha=reg,tol=10-10).fit(xtt,yt)
    
    tw = np.linspace(-30.0,30,n)
    tb = np.linspace(-4.0,12.0,n)
    
    tw_mg,tb_mg=np.meshgrid(tw,tb)
    J_mg= loss2(reg,tw_mg,tb_mg,xt,yt)[0]
    w0= [tw[90]]
    b0= [tb[90]]
    l0 =[loss2(reg,w0[-1],b0[-1],xt,yt)[0]]
    
    Jmin=loss2(reg,ridge.coef_,ridge.intercept_,xt,yt)[0]

    for i in range(0,ig):
        wc=w0[-1]
        bc=b0[-1]
        w0.append(wc-eta*loss2(reg,wc,bc,xt,yt)[1])
        b0.append(bc-eta*loss2(reg,wc,bc,xt,yt)[2])
        l0.append(loss2(reg,w0[-1],b0[-1],xt,yt)[0])
    
    fig = go.Figure()
    fig.add_trace(go.Surface(x=tw_mg, y=tb_mg, z=J_mg, cmid=0, colorscale="Jet",opacity=0.5))
    fig.add_trace(go.Scatter3d(x=[0.5], y=[3.5], z=[0.0],mode='markers',marker_size=5,marker_color='red'))
    fig.add_trace(go.Scatter3d(x=ridge.coef_, y=[ridge.intercept_], z=[Jmin[0]],mode='markers',marker_size=8,marker_color='blue',opacity=0.75))
    fig.add_trace(go.Scatter3d(x=w0, y=b0, z=l0, marker_color="green",opacity=0.9,marker_size=4))
    fig.update_layout(height=500, width=800, margin=dict(l=35, r=30, b=45, t=60),showlegend=False)
    fig.show()

In [23]:
@interact(nb_point=(1,20,1),bruit=(0.02,0.05,0.005),eta=(0.2,2.0,0.1),ig=(0,100,5),reg=(0.0,1.0,0.01))
def plot9(nb_point=10,bruit=0.05,eta=0.1,ig=0,reg=0):
    plot_gradient2(nb_point,bruit,eta,ig,reg)

interactive(children=(IntSlider(value=10, description='nb_point', max=20, min=1), FloatSlider(value=0.05, desc…

**Conclusion**:

En ajoutant la contrainte faible, on retrouve un problème avec un $\color{red}{\text{unique minimum}}$.

Il n'existe plus une infinité de modèles (de jeux de paramètres) qui approche les données mais **un seul** qui approche les données avec un peu de contrainte sur les poids.

Avant, pour $d>n$, on avait une infinité de modèles possibles dont le bon.

Ici $\color{red}{\text{le minimum de problème de minimisation n'est plus la vraie solution}}$. On a donc un seul modèle possible qui n'est pas le bon mais $\color{red}{\text{qui est proche du bon pour $\lambda$ petit}}$.

**Exemple en grande dimension**:

On regarde $n=100$ le nombre d'échantillons et on fait varier la dimension.

On va regarder l'effet de la régularisation. En rouge le cas sans régularisation

In [24]:
def running_mean(x, N): ## Moyenne glissante
    out = np.zeros_like(x, dtype=np.float64)
    dim_len = len(x)
    for i in range(dim_len):
        if N%2 == 0:
            a, b = i - (N-1)//2, i + (N-1)//2 + 2
        else:
            a, b = i - (N-1)//2, i + (N-1)//2 + 1
        #cap indices to min and max indices
        a = max(0, a)
        b = min(dim_len, b)
        out[i] = np.mean(x[a:b])
    return out

In [25]:
def plot_overfitting_dim2(sigma,dim): ## affiche les erreurs pour une regréssion classique
    lamd_list = np.linspace(0.0,10,200)
    beta= np.linspace(-0.2,0.2,dim) ### on se fixe une fonction particulière f(x)=\beta x+\alpha
    alpha = -1.0
    n = 100 
    E=[]; N=[]
    X,Y,eps= generate_data(sigma,beta,alpha,n,dim)
    for il in range(0,len(lamd_list)):
        Error,ErrorQuad,normp = errorR(lamd_list[il],beta,alpha,X,Y,n,dim)
        E.append(Error); N.append(normp)

    fig = make_subplots(rows=1, cols=2,
                        subplot_titles=("Erreur sur nouvelles données Ridge", 
                                        "Norme Poids")
                        ) 
    fig.add_trace(go.Scatter(x=lamd_list, y=E,line_width=3,line_color='blue'), row=1, col=1)
    fig.add_trace(go.Scatter(x=lamd_list, y=E[0]*np.ones(len(lamd_list)),line_width=3,line_color='red'), row=1, col=1)
    fig.add_trace(go.Scatter(x=lamd_list, y=running_mean(E,10),line_width=3,line_color='yellow'), row=1, col=1)
    
    
    fig.add_trace(go.Scatter(x=lamd_list, y=N,line_width=3,line_color="blue"), row=1, col=2)
    fig.update_layout(height=350, width=950, margin=dict(l=35, r=30, b=45, t=60),
                  title_text="Régression Ridge")
    fig.update_layout(showlegend=False)
    fig.show()

In [26]:
@interact(sigma=(0.02,0.05,0.005),dim=(20,400,10))
def plot10(sigma=0.05,dim=20):
    plot_overfitting_dim2(sigma,dim)

interactive(children=(FloatSlider(value=0.05, description='sigma', max=0.05, min=0.02, step=0.005), IntSlider(…

On voit, qu'un certain nombre de valeur de $\lambda$ (paramètre de régularisation) permettent de baisser l'erreur de $\color{red}{\text{de généralisation baisse}}$.

Pour choisir un modèle.
On teste plusieurs valeurs de $\lambda$ et on les compare sur un jeux de données de **validation** (pas utilisé pour entraîner le modèle) et on choisit le meilleur.

### Régression Lasso et elasticNet

Il existe d'autre type de régression
- régression **Lasso**
- régression **elasticNet**

**Régression Lasso**:

On résout

$$
\operatorname{min}_{\theta}J(\theta)=\sum_{i=1}^n d_2(y_i,f_{\theta}(x_i))^2 +\lambda d_1(\theta,0)^2
$$

avec $d_1(.,.)$ la distance de Manhattan.

Ici cela ne contraint pas les paramètres à être petit mais cela contraint un certain nombre de paramètres à être nul. Plus $\lambda$ est grand plus un nombre important de paramètres sont nuls.

**Hypothèse de Parcimonie**:

on a $f(x)=\sum_{i=1}^d a_i x_i+a_0$ avec $d>>1$.

$f(x)$ est parcimonieuse si beaucoup de coefficients $a_i$  sont nuls.

La $\color{red}{\text{régression Lasso permet de pouvoir capturer ce genre de fonction}}$ la ou une régression ridge va chercher un bon modèle sans mettre les coefficients à zéro.

Exemple:
    
$f(x)=x_2-2x_4+x_{m-2}$

In [27]:
def generate_dataLasso(m):
    X = np.zeros((100,m)) ## creation de la matrice à n exemple de dimension m
    Y = np.zeros(100) ## creation de la matrice à n exemple de dimension l
    eps = randn.normal(0.0,0.05,100) ## vecteur des bruits
    
    for i in range(0, 100):
        X[i,:]=randn.uniform(0.0,2.0,m) # m nombre aléatoire entre 0 et 1
        Y[i]= X[i,2] - 2.0*X[i,4] + 1.5*X[i,m-2]  +eps[i]
    scaler = preprocessing.StandardScaler().fit(X)
    return X,Y
    
def Ridge_Lasso_error(lam,X,Y,m):
    Y_test_ref = np.zeros(50); Xnew = np.zeros((50,m)) 
    for i in range(0, 50):
        Xnew[i,:]=randn.uniform(0.0,2.0,m)   
        Y_test_ref[i]= Xnew[i,2] - 2.0*Xnew[i,4] + 1.5*Xnew[i,m-2]

    regR = Ridge(alpha=lam,solver="svd",tol=0.0000001).fit(X,Y)
    if lam>0.0:
        regL = Lasso(alpha=lam,tol=0.000001).fit(X,Y)
    else:
        regL = Ridge(alpha=0.0,solver="svd",tol=0.000001).fit(X,Y)
        
    
    ErrorR = np.mean((Y_test_ref - regR.predict(Xnew))**2)
    normp = np.linalg.norm(regR.coef_,2)
    ErrorL = np.mean((Y_test_ref - regL.predict(Xnew))**2)
    coefs_nuls=0
    for i in range(0,len(regL.coef_)):
        if abs(regL.coef_[i])<0.000000001:
            coefs_nuls+=1
    if abs(regL.intercept_)<0.000000001:
        coefs_nuls+=1
 
    return ErrorR,normp,ErrorL,coefs_nuls

In [28]:
def plot_overfitting_lasso(sigma,dim): ## affiche les erreurs pour une regréssion classique
    lamd_list = np.linspace(0.0,0.05,100)
    E=[]; N=[]; E2=[]; C=[]
    X,Y= generate_dataLasso(dim)
    for il in range(0,len(lamd_list)):
        ErrorR,normp,ErrorL,coefnuls = Ridge_Lasso_error(lamd_list[il],X,Y,dim)
        E.append(ErrorR); N.append(normp)
        E2.append(ErrorL); C.append(coefnuls)

    fig = make_subplots(rows=2, cols=2,
                        subplot_titles=("Erreur sur nouvelles données Ridge", 
                                        "Norme Poids", 
                                        "Erreur sur nouvelles données Lasso",
                                        "Proportion poids nuls")
                        ) 
    fig.add_trace(go.Scatter(x=lamd_list, y=E,line_width=3,line_color='blue'), row=1, col=1)
    fig.add_trace(go.Scatter(x=lamd_list, y=E[0]*np.ones(len(lamd_list)),line_width=3,line_color='red'), row=1, col=1)
    fig.add_trace(go.Scatter(x=lamd_list, y=running_mean(E,10),line_width=3,line_color='orange'), row=1, col=1)
    
    
    fig.add_trace(go.Scatter(x=lamd_list, y=N,line_width=3,line_color="blue"), row=1, col=2)
    
    
    fig.add_trace(go.Scatter(x=lamd_list, y=E2,line_width=3,line_color='blue'), row=2, col=1)
    fig.add_trace(go.Scatter(x=lamd_list, y=E2[0]*np.ones(len(lamd_list)),line_width=3,line_color='red'), row=2, col=1)
    fig.add_trace(go.Scatter(x=lamd_list, y=running_mean(E2,10),line_width=3,line_color='orange'), row=2, col=1)
    
    
    fig.add_trace(go.Scatter(x=lamd_list, y=C,line_width=3,line_color="blue"), row=2, col=2)
    fig.update_layout(height=500, width=950,
                  title_text="Régression Ridge vs régression Lasso")
    fig.update_layout(showlegend=False)
    fig.show()
    ##TOOOO DOOO

In [29]:
dim = widgets.IntSlider(value=20,min=10,max=200,step=10,description="dimension régression")
sigma = widgets.IntSlider(value=0.05,min=0.01,max=0.1,step=0.01,description="dimension régression")

ui11= widgets.VBox([sigma,dim])

@interact(sigma=(0.02,0.05,0.005),dim=(20,400,10))
def plot11(sigma=0.05,dim=20):
    plot_overfitting_lasso(sigma,dim)

interactive(children=(FloatSlider(value=0.05, description='sigma', max=0.05, min=0.02, step=0.005), IntSlider(…

On voit que la régression permet de bien $\color{red}{\text{capturer la fonction parcimonieuse}}$ contrairement à la régularisation Ridge.

Encore une fois on peut comparer les modèles sur des **données de validation**.

## Régression a Noyaux

Si $f(x)$ est linéaire ou proche la régression linéiare est **adaptée**. 

**Cas nonlinéaire**:

$$
f(x)=x^2+sin(x), \quad f(x,y)=x*y+y^3cos(x), \quad\mbox{etc}
$$

On fait comment ?

**Problème**: on connait pas $\phi$.

Théorie des noyaux reproduisant (mathématique compliquée):

On se donne des points $(x_1,..x_n)$. On peut approcher une déformation par

$$
\phi(x) \approx \sum_{i=1}^n k(x,x_i)
$$

avec $k(x,y)$ une fonction dite noyau.

Solution possible: $\color{red}{\text{méthode à noyau}}$.

**Idée**: on transforme les données et on espère qu'après cette transformation la fonction soit presque linéaire.

Exemple:

$$
f(x,y,z)=sin(x)+1.2cos(y) -sin(z)+ 0.001sin(z)^2
$$

Si on prend la transformation $(x,y,z):\rightarrow \phi(x,y,z)=(\phi_1,\phi_2,\phi_3)=(sin(x),cos(y),cos(z))$ on obtient:


$$
f(\phi_1,\phi_2,\phi_3)=\phi_1+1.2\phi_2-\phi_3+0.001\phi_3^2\approx\phi_1+1.2\phi_2-\phi_3
$$

On voit donc qu'une $\color{red}{\text{régression linéaire marchera très bien}}$ sur $f(\phi_1,\phi_2,\phi_3)$.

**Exemple**: on veut approcher 

$$
f(x)=\frac12 x^2 - \frac1{10}\sqrt{3x^5}
$$

Si on prend la transformation $(z_1,z_2)=(x^2,\sqrt{3x^5})$ on voit qu'on a une relation linéaire 

$$
g(z_1,z_2)= \frac12 z_1 - \frac1{10} z_2
$$

On voit que la $\color{red}{\text{transformation augmente de dimension}}$ (1 vers 2).


In [30]:
def plot_transformation(nb_point): ## affiche les erreurs pour une regréssion classique
    x=np.linspace(0.0,1.0,100)
    y=0.5*x*x-0.1*np.sqrt(3.0*x*x*x*x)
    z=np.zeros(100)
    
    z_1=x*x
    z_2=np.sqrt(3.0*x*x*x*x)
    Z_1,Z_2=np.meshgrid(z_1,z_2)
    Z_3=0.5*Z_1-0.1*Z_2
    z_3=0.5*z_1-0.1*z_2
    
    x_ex=[]
    y_ex=[]
    z_ex=[0.0 for i in range(0,nb_point)]
    z1_ex=[]
    z2_ex=[]
    z3_ex=[]
    for i in range(0,nb_point):
        x_ex.append(x[99-i*int(100/nb_point)])
        y_ex.append(0.5*x_ex[-1]*x_ex[-1]-0.1*np.sqrt(3.0*x_ex[-1]**4.0))
        z1_ex.append(x_ex[-1]*x_ex[-1])
        z2_ex.append(np.sqrt(3.0*x_ex[-1]**4.0))
        z3_ex.append(0.5*z1_ex[-1]-0.1*z2_ex[-1])

    fig = go.Figure()
    fig.add_trace(go.Scatter3d(x=x, y=y, z=z,opacity=0.5,marker_size=2))
    fig.add_trace(go.Scatter3d(x=z_1, y=z_2, z=z_3,opacity=0.7,marker_size=3,marker_color='blue'))
    fig.add_trace(go.Surface(x=Z_1, y=Z_2, z=Z_3, colorscale="Jet",opacity=0.5))
    for i in range(0,nb_point):   
        xloc=[x_ex[i],z1_ex[i]]
        yloc=[y_ex[i],z2_ex[i]]
        zloc=[z_ex[i],z3_ex[i]]
        fig.add_trace(go.Scatter3d(x=xloc, y=yloc, z=zloc, marker_color="green",opacity=0.9,marker_size=4))
    fig.update_layout(showlegend=False)

    fig.show()
    ##TOOOO DOOO

In [31]:
plot_transformation(20)

**Régression à noyaux**

$$
\operatorname{min}_{\theta}J(\theta)=\sum_{i=1}^n d_2(y_i,f_{\theta}(x_i))^2
$$

avec

$$
f_{\theta}(x)=\sum_{i=1}^d \omega_i \phi(x_i), \quad\mbox{avec}\quad \phi(x)= \sum_{i=j}^n a_j k(x,x_j)
$$

Beaucoup de noyaux possibles (https://scikit-learn.org/stable/modules/classes.html#module-sklearn.metrics.pairwise). Exemple:

$$
k(x,y)=exp^{-\gamma d(x,y)_1}, \quad k(x,y)=exp^{-\gamma d(x,y)_2^2}
$$

In [32]:
import numpy as np
from sklearn.kernel_ridge import KernelRidge
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D 

def f(x):
    return -np.sin(x[0]*x[1]) + 1.5*np.cos(x[1])

def plot_kernel(n_p,k1):
    X = np.zeros((n_p,2))
    X[:,0] = np.linspace(0.0,2.0,n_p) 
    X[:,1] = np.linspace(0.0,2.0,n_p)
    X[:,0] = np.random.normal(X[:,0],0.05,n_p)
    X[:,1] = np.random.normal(X[:,1],0.05,n_p)
    Y= np.array([ f(X[i,:]) for i in range(0,n_p)])

    X_t = np.zeros((20,2))
    X_t[:,0] = np.linspace(0.0,2.0,20)
    X_t[:,1] = np.linspace(0.0,2.0,20)

    reg1 = KernelRidge(kernel="linear",alpha=0.01).fit(X,Y)
    reg2 = KernelRidge(kernel=k1,alpha=0.01).fit(X,Y)
    Y1_t =reg1.predict(X_t)
    Y2_t =reg2.predict(X_t)

    fig = make_subplots(rows=1, cols=2, specs=[[{"type": "scene"}, {"type": "scene"}]]) 
    fig.add_trace(go.Scatter3d(x=X[:, 0], y=X[:, 1], z=Y,
                               mode='markers',marker_size=5,marker_color='blue'), row=1, col=1 )
    fig.add_trace(go.Scatter3d(x=X_t[:, 0], y=X_t[:, 1], z=Y1_t,
                               line_width=1,line_color='red',opacity=0.5), row=1, col=1)
    
    fig.add_trace(go.Scatter3d(x=X[:, 0], y=X[:, 1], z=Y,
                            mode='markers',marker_size=5,marker_color='blue'), row=1, col=2 )
    fig.add_trace(go.Scatter3d(x=X_t[:, 0], y=X_t[:, 1], z=Y2_t,
                               line_width=1,line_color='red',opacity=0.5), row=1, col=2)
    fig.update_layout(height=500, width=950,
                  title_text="Noyau linéaire vs autre")
    fig.update_layout(showlegend=False)
    fig.show()

In [33]:
@interact(n_p=(10,100,5),k1=['linear', 'cosine','sigmoid','polynomial', 'rbf'])
def plot12(n_p=20,k1='linear'):
    plot_kernel(n_p,k1)

interactive(children=(IntSlider(value=20, description='n_p', min=10, step=5), Dropdown(description='k1', optio…

Pour visualiser on regarde ce que les méthodes à noyaux pourraient apporter en classification.

L'idée est la même, on applique une $\color{red}{\text{transformation}}$ puis on sépare avec un modèle linéaire.

In [34]:
def func1(z):
    return z/5.0 + 0.25*z/np.sqrt(z[0]*z[0]+z[1]*z[1])

def func2(z):
    return z/5.0 + z/np.sqrt(z[0]*z[0]+z[1]*z[1])

def transformation(x,y):
    return [x**2.0,y**2.0,np.sqrt(1.5*x*y+1.2)]

In [35]:
def plot_kernel_classfication():
    mean = [0, 0]
    cov = [[0.04, 0], [0, 0.04]] 
    X  = np.random.multivariate_normal(mean, cov, 200)
    Z= copy.copy(X)
    Z2= copy.copy(X)
    Z_add = np.zeros(200)
    Z2_add = np.zeros(200)
    for i in range(0,200):
        Z[i,:]=func1(X[i,:])
        Z2[i,:]=func2(X[i,:])
    
        TX,TY,TZ=transformation(Z[:,0],Z[:,1])
        TX2,TY2,TZ2=transformation(Z2[:,0],Z2[:,1])
    
    fig = make_subplots(
        rows=1, cols=2,
        specs=[[{"type": "bar"}, {"type": "scene"}]],
    ) 
    fig.add_trace(go.Scatter(x=Z[:, 0], y=Z[:, 1],
                               mode='markers',marker_size=5,marker_color='blue'), row=1, col=1 )
    fig.add_trace(go.Scatter(x=Z2[:, 0], y=Z2[:, 1],
                               mode='markers',marker_size=5,marker_color='red'), row=1, col=1 )
    fig.add_trace(go.Scatter3d(x=TX[:], y=TY[:], z=TZ[:],
                               mode='markers',marker_size=5,marker_color='blue'), row=1, col=2 )
    fig.add_trace(go.Scatter3d(x=TX2[:], y=TY2[:], z=TZ2[:],
                               mode='markers',marker_size=5,marker_color='red'), row=1, col=2 )
    fig.update_layout(showlegend=False)

    fig.show()

In [36]:
plot_kernel_classfication()

## Conclusion

- La régression linéaire permet de construire, pour toute dimension de x, des modèles approchant

$$
y=f(x)+ \epsilon
$$

à partir d'exemples $(x_1,...x_n)$ et $(y_1,...,y_n)$

- La méthode marche bien pour des fonctions linéaires ou presque linéaires.


- en grande dimension $d>>1$, on a souvent $d>n$. Dans ce cas on risque le **sur-apprentissage**. Le modèle est tellement riche (car beaucoup de paramètres ou a des grandes capacités de représentation) qu'il apprend parfaitement les données.


- Si **sur-apprentissage** on risque une mauvaise généralisation.

- Les **méthodes de régularisation** limitent le problème.


- La **régression à noyaux** qui applique une transformation aux données permet de traiter des fonctions plus générales (non linéaires).